In [6]:
import IPython.display as ipd
import torch
import commons
import utils
from models import SynthesizerTrn
from text.symbols import symbols
from text import text_to_sequence
import re
model_name = 'ja'
config_file = f"configs/{model_name}.json"
model_file = utils.latest_checkpoint_path(f"./logs/{model_name}/")
device = 'cpu' # cuda:0

hps = utils.get_hparams_from_file(config_file)

text = '''
[KO]안녕하세요. 만나서 반가워요...[KO]
[JA]こんにちは. お会いできて嬉しいです...[JA]
[EN]Hello, Nice to meet you...[EN]
[ID]Halo. Senang bertemu dengan Anda...[ID]
[VI]Xin chào. Rất vui được gặp bạn...[VI]
[RU]привет. рад встрече...[RU]
[TR]Merhaba. Tanıştığıma memnun oldum...[TR]
[ES]Hola. encantado de conocerlo..[ES]
[PT]olá. prazer em conhecê-lo...[PT]
[IT]Ciao. piacere di conoscerti...[IT]
[PO]Witam. Miło mi cię poznać...[PO]
[DE]Hallo. Schön, dich kennenzulernen...[DE]
[NL]Hallo. Aangenaam...[NL]
[UK]привіт. приємно познайомитись...[UK]
[SV]Hallå. Trevligt att träffas...[SV]
[CS]Ahoj. Rád vás poznávám...[CS]
[FI]Kamusta. Ikinagagalak kitang makilala...[FI]
[LA]Salve. Vos noscere...[LA]
[HU]Helló. örvendek...[HU]
'''
# text = '''
# 훈민정음해례본은 세종이 직접 서문을 쓰고, 정인지를 비롯한 신하들에게 글자에 대한 설명을 적게 한 것으로, 1940년 안동에서 발견되었다. 
# 즉 이 책이 발견됨으로써 한글이 얼마나 과학적인 원리로 만들어졌는지 밝혀지게 된 것이다. 
# 1962년 12월 10일 국보 제70호로 지정된 훈민정음해례본은 목판본으로 이루어져 있으며, 서울시 성북구 성북동에 위치한 간송미술관에 소장되어 있다. 
# 훈민정음해례본은 1997년 유네스코 세계기록유산에 등재되었으며, 우리나라는 훈민정음해례본의 발간 일을 계산해 양력 10월 9일을 한글날로 지정하고 1946년부터 매년 국가 기념행사를 개최하고 있다.
# '''

def get_text(text, hps):
    text_norm = text_to_sequence(text, hps.data.text_cleaners)
    if hps.data.add_blank:
        text_norm = commons.intersperse(text_norm, 0)
    text_norm = torch.LongTensor(text_norm)
    return text_norm

net_g = SynthesizerTrn(
    len(symbols),
    hps.data.filter_length // 2 + 1,
    hps.train.segment_size // hps.data.hop_length,
    **hps.model).to(device)
_ = net_g.eval()

_ = utils.load_checkpoint(model_file, net_g, None)

speed = 1

text = text.strip()
text = re.sub('[\n]', '', text)
stn_tst = get_text(text, hps)
with torch.no_grad():
    x_tst = stn_tst.to(device).unsqueeze(0)
    x_tst_lengths = torch.LongTensor([stn_tst.size(0)]).to(device)
    audio = net_g.infer(x_tst, x_tst_lengths, noise_scale=.667, noise_scale_w=0.8, length_scale=1/speed)[0][0,0].data.cpu().float().numpy()
ipd.display(ipd.Audio(audio, rate=hps.data.sampling_rate))

Mutli-stream iSTFT VITS
ㅇㅏㄴㄴㅣㅓㅇㅎㅏㅅㅔㅇㅣㅗ. ㅁㅏㄴㄴㅏㅅㅓ ㅂㅏㄴㄱㅏㅇㅜㅓㅇㅣㅗ... ㅋㅗㄴㄴㅣㅊㅣㅇㅗㅏ. ㅇㅗㅇㅏㅇㅣㄷㅔㅋㅣㅌㅔ ㅇㅜㄹㅔㅅㅣㅇㅣㄷㅔㅅㅡ... ㅎㅓㄹㄹㅗ, ㄴㅏㅇㅣㅅㅡ ㅌㅜ ㅁㅣㅌㅡ ㅇㅣㅜ... ㅎㅏㄹㅗ. ㅅㅔㄴㅏㅇ ㅂㅔㄹㅌㅔㅁㅜ ㄷㅔㅇㅏㄴ ㅇㅏㄴㄷㅏ... ㅆㅣㄴ ㅉㅏㅇㅗ. ㄹㅓㄷ ㅃㅜㅇㅣ ㄷㅡㅇㅓㄱ ㄲㅏㅂ ㅃㅏㄴ... ㅍㅡㄹㅣㅂㅔㅌㅡ. ㄹㅏㅌㅡ ㅍㅡㅅㅡㅌㅡㄹㅔㅊㅔ... ㅁㅔㄹㅡㅎㅏㅂㅏ. ㅌㅏㄴㅡㅅㅣㅜㅌㅡㅇㅡㅁㅏ ㅁㅔㅁㄴㅜㄴ ㅇㅗㄹㄷㅜㅁ... ㅇㅗㄹㄹㅏ. ㅇㅔㅇㅋㅏㄴㅌㅏㄷㅗ ㄷㅔ ㅋㅗㄴㅗㅅㅔㄹㅡㄹㄹㅗ.. ㅇㅗㄹㄹㅏ. ㅍㅡㄹㅏㅈㅔㄹㅡ ㅇㅣㅇ ㅋㅗㄴㅣㅔㅅㅔㅇㅡㄹㄹㅜ... ㅊㅏㅇㅗ. ㅍㅣㅇㅏㅊㅔㄹㅔ ㄷㅣ ㅋㅗㄴㅗㅅㅣㅔㄹㅡㅌㅣ... ㅂㅣㅌㅏㅁ. ㅁㅣㅇㅜㅓ ㅁㅣ ㅊㅣㅇㅔ ㅍㅗㅈㅡㄴㅏㅊㅣ... ㅎㅏㄹㄹㅗ. ㅅㅗㅣㄴ, ㄷㅣㅎㅣ ㅋㅔㄴㅔㄴㅊㅜㄹㄹㅔㄹㅡㄴㅔㄴ... ㅎㅏㄹㄹㅗ. ㅇㅏㄴㅎㅔㄴㅏㅁ... ㅍㅡㄹㅣㅂㅣㅌㅡ. ㅍㅡㄹㅣㅇㅣㅔㅁㄴㅗ ㅍㅗㅈㅡㄴㅏㅇㅣㅗㅁㅣㅌㅣㅅㅡ... ㅎㅏㄹㄹㅗ. ㅌㅡㄹㅔㅂㅡㄹㄹㅣㄱㅌㅡ ㅇㅏㅌㅡ ㅌㅡㄹㅔㅍㅏㅅㅡ... ㅇㅏㅎㅗㅇㅣ. ㄹㅏㅌㅡ ㅂㅏㅅㅡ ㅍㅗㅈㅡㄴㅏㅂㅏㅁ... ㅋㅏㅁㅜㅅㅡㅌㅏ. ㅇㅣㅋㅣㄴㅏㄱㅏㄱㅏㄹㄹㅏㅋㅡ ㅋㅣㅌㅏㅇ ㅁㅏㅋㅣㄹㄹㅏㄹㄹㅏ... ㅅㅏㄹㅂㅔ. ㅂㅗㅅㅡ ㄴㅗㅅㅡㅋㅔㄹㅔ... ㅎㅔㄹㄹㅗ. ㅇㅗㅣㄹㅡㅂㅔㄴㄷㅔㅋㅡ...
